In [2]:
import os
import numpy as np, pandas as pd, seaborn as sns, matplotlib.pyplot as plt, plotly.express as px

In [83]:
from IPython.display import display, HTML

In [3]:
import datetime

In [38]:
from statsmodels.graphics.tsaplots import plot_acf

In [4]:
pd.set_option('display.max_rows',500)
sns.set(rc={'figure.figsize':(10,6)})

In [5]:
today = datetime.datetime.today()

In [6]:
sunspot = pd.read_csv('Datasets/sunspots-SN_d_tot_V2.0.csv',delimiter=';',names=['year','month','day','fractional_date','daily_sunspots','stDev','#observations','definitive'])

In [7]:
#-1 - missing value for Daily Sunspots
#For Definitive/Provisional indicator, '1' indicates that the value is definitive. '0' indicates that the value is still provisional.

In [43]:
sunspot.tail(10)

year  month  day  fractional_date  daily_sunspots  stDev  \
73890  2020      4   21         2020.305               0    0.0   
73891  2020      4   22         2020.307               0    0.0   
73892  2020      4   23         2020.310               0    0.0   
73893  2020      4   24         2020.313               0    0.0   
73894  2020      4   25         2020.316               6    0.4   
73895  2020      4   26         2020.318              14    1.0   
73896  2020      4   27         2020.321              29    2.0   
73897  2020      4   28         2020.324              15    2.6   
73898  2020      4   29         2020.327              24    1.6   
73899  2020      4   30         2020.329              20    1.2   

       #observations  definitive       date  variance  daily_sunspot_var  \
73890             37           0 2020-04-21      0.00         -79.078043   
73891             43           0 2020-04-22      0.00         -79.078043   
73892             43           0 2020-04-23      0.00         -79.078043   
73893             42           0 2020-04-24      0.00         -79.078043   
73894             22           0 2020-04-25      0.16         -73.078043   
73895             23           0 2020-04-26      1.00         -65.078043   
73896             20           0 2020-04-27      4.00         -50.078043   
73897             18           0 2020-04-28      6.76         -64.078043   
73898             22           0 2020-04-29      2.56         -55.078043   
73899             20           0 2020-04-30      1.44         -59.078043   

       daily_sunspot_var_abs  
73890              79.078043  
73891              79.078043  
73892              79.078043  
73893              79.078043  
73894              73.078043  
73895              65.078043  
73896              50.078043  
73897              64.078043  
73898              55.078043  
73899              59.078043

In [10]:
sunspot.definitive.value_counts()

1    73779
0      121
Name: definitive, dtype: int64

In [11]:
sunspot['date'] = pd.to_datetime((sunspot['year'].astype(str)+sunspot['month'].astype(str)+sunspot['day'].astype(str)),format='%Y%m%d',errors='coerce')

In [15]:
sunspot['obs_var'] = sunspot['stDev']*sunspot['stDev']

In [23]:
sunspot['daily_sunspot_var'] = sunspot['daily_sunspots'] - sunspot['daily_sunspots'].mean()

In [26]:
sunspot['daily_sunspot_var_abs'] = abs(sunspot['daily_sunspots'] - sunspot['daily_sunspots'].mean())

In [12]:
#sunspot = sunspot.loc[sunspot['date']<=today] # remove some incorrect dates

In [14]:
fig = px.scatter(sunspot, x='date', y='daily_sunspots',width=1200, height=600)
fig.show()

In [183]:
acf = pd.concat([sunspot['date'].dt.strftime('%Y-%m-%d'),sunspot['daily_sunspots']],axis=1)

In [37]:
fig = px.scatter(sunspot, x='date', y='stDev',width=1200, height=600)
fig.show()

In [194]:
def autocorrelation(timelist,lags):
    #lag of one period
    temp1 = pd.DataFrame()
    temp1 = timelist.copy()

    temp2 = []

    for lag in range(lags):

        val_mean = temp1.iloc[:,1].mean()

        colname_lag = 'date-{}'.format(lag+1)
        temp1[colname_lag] = temp1.iloc[:,1].shift(periods=lag+1)

        colname_mean_diff = 'mean_diff-{}'.format(lag+1)
        temp1[colname_mean_diff] = temp1.iloc[:,1] - val_mean

        colname_lag_mean_diff = 'lag_mean_diff-{}'.format(lag+1)
        temp1[colname_lag_mean_diff] = temp1[colname_lag] - val_mean

        colname_square_diff = 'mean_square_diff-{}'.format(lag+1)
        temp1[colname_square_diff] = temp1[colname_mean_diff]*temp1[colname_mean_diff]

        colname_autocov = 'autocov-{}'.format(lag+1)
        temp1[colname_autocov] = temp1[colname_mean_diff]*temp1[colname_lag_mean_diff]

                 
       # print(sum(temp1[colname_autocov]))

        temp2.append(temp1[colname_autocov].sum()/temp1[colname_square_diff].sum())

    #display(HTML(temp1.tail(10).to_html()))

  #  print(temp1.head())
    
    temp2 = pd.DataFrame(temp2,columns =['autc'])

    return(temp2)

In [204]:
autc = autocorrelation(acf,4400)

MemoryError: Unable to allocate 5.50 GiB for an array with shape (9997, 73882) and data type float64

In [ ]:
autc.info()

In [ ]:
fig = px.bar(autc,x=autc.index,y='autc',labels = {'x':'Lag'})

fig.update_layout(
    title="Plot Title",
    xaxis_title="Lag",
    yaxis_title="ACF",
)

fig.show()

In [184]:
acf

date  daily_sunspots
0      1818-01-01              -1
1      1818-01-02              -1
2      1818-01-03              -1
3      1818-01-04              -1
4      1818-01-05              -1
...           ...             ...
73895  2020-04-26              14
73896  2020-04-27              29
73897  2020-04-28              15
73898  2020-04-29              24
73899  2020-04-30              20

[73882 rows x 2 columns]